In [1]:
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from tqdm import tqdm

import scipy.stats as st
from statsmodels.stats.power import tt_ind_solve_power
from statsmodels.stats.power import zt_ind_solve_power
from statsmodels.stats.proportion import proportion_effectsize
from statsmodels.stats import proportion
from statsmodels.stats.meta_analysis import effectsize_smd

from statsmodels.stats.proportion import proportion_effectsize

from typing import Union

from scipy import stats
from math import asin

import math

# Задание
На основе выбранных продуктов из первого вебинара, выберите 2 A/B-теста и составьте план эксперимента, чтобы избежать Peeking Problem

Распишите, какие метрики и как вы будете анализировать

### Для анализа я выбрала сайт citilink.ru - интернет-магазин техники, электроники, товаров для дома и ремонта.

# Чек-лист (сокращенный)
## 1. Формирование и приоретизация гипотез
* 1.1 Составление и приоретизация бэклога экспериментов
## 2. Проектирование дизайна эксперимента для проверки гипотез
* 2.1 Сформулирована цель и гипотеза
* 2.2 Выбраны метрики и длительность эксперимента
* 2.3 Проверини инфраструктура
* 2.4 Все ответственные за эксперимент оповещены не позднее чем за один день до начала эксперимента
## 3. Запуск теста
* 3.1 Выполнено корректное сплитование юзеров
* 3.2 Все стейкхолдеры знают о запуске теста и его деталях
* 3.3 Создан дашборд.
## 4. Сбор и анализ данных. Интерпретация результата
* 4.1 Не делаются финальные выводы на основе промежуточных результатов
* 4.2 Посчитаны результаты и сделано описание
* 4.3 коллеги оповещены, когда результат готов
## 5. Принятие решения на основе результатов теста
* 5.1 Принято решение по результатам теста

### 1. Формирование и приоретизация гипотез
На основе анализа сайта было выдвинуто несколько гипотез и проведен их скоринг:
<table>
    <tr>
        <td>№</td>
        <td>Idea</td>
        <td>Impact</td>
        <td>Confidence</td>
        <td>Ease</td>
        <td>ICE Score</td>
        <td>Priority</td>
    </tr>
    <tr>
        <td>1</td>
        <td>Если разместить основной каталог товаров слева на стартовой странице для новых пользователей , то мы уменьшим Churn Rate на 10% потому что упростим поиск необходимых товаров. Непонятность отпугивает потенциальных покупателей</td>
        <td>4</td>
        <td>6</td>
        <td>5</td>
        <td>120</td>
        <td>5</td>
    </tr>
    <tr>
        <td>2</td>
        <td>Если уменьшить поле рекламмы и тем самым приподнять популярные категории на первую страницу для всех пользователей, то мы увеличим конверсию в покупку на 7% потому что пользователю будет легче найти интересующий его товар.</td>
        <td>6</td>
        <td>5</td>
        <td>7</td>
        <td>210</td>
        <td>4</td>
    </tr>
    <tr>
        <td>3</td>
        <td>Если добавить справочную информацию по параметрам сравнения в разделе "Сравнение товаров" для всех пользователей, то мы увеличим конверсию в покупку на 13% потому что пользователь любит платить за то, что он понимает, а непонятные термины и характеристики его отпугивают.</td>
        <td>7</td>
        <td>7</td>
        <td>7</td>
        <td>343</td>
        <td>2</td>
    </tr>
    <tr>
        <td>4</td>
        <td>Если сделать систему настройки фильтров при подборе товаров более простой и понятной для всех пользователей, то мы увеличим время проведенное на сайте на 10% потому что пользователю будет проще искать необходимый товар.</td>
        <td>8</td>
        <td>9</td>
        <td>5</td>
        <td>360</td>
        <td>1</td>
    </tr>
    <tr>
        <td>5</td>
        <td>Если улучшить загрузку страницы "корзины" для всех пользователей сайта, то мы увеличим конверсию в покупку на 20% потому что при "корявой" загрузке нет никакого желания офорлять заказ</td>
        <td>10</td>
        <td>10</td>
        <td>3</td>
        <td>300</td>
        <td>3</td>
    </tr>
</table>

В результате было выбрано для исследования 2 гипотезы:
1. Если сделать систему настройки фильтров при подборе товаров более простой и понятной для всех пользователей, то мы увеличим время проведенное на сайте на 15% потому что пользователю будет проще искать необходимый товар.
2. Если добавить справочную информацию по параметрам сравнения в разделе "Сравнение товаров" для всех пользователей, то мы увеличим конверсию в покупку на 13% потому что пользователь любит платить за то, что он понимает, а непонятные термины и характеристики его отпугивают.

## `Гипотеза 1`
### 2. Дизайн эксперимента 1
***Гипотеза 1:*** Если сделать систему настройки фильтров при подборе товаров более простой и понятной для всех пользователей, то мы увеличим время проведенное на сайте на 10% потому что пользователю будет проще искать необходимый товар.

***Что делаем:***
* *Контрольная версия* - оставляем систему настройки фильтров без изменения.
* *Тестовая версия* - вводим упрощенную систему настройки фильтров при подборе товара.

***На каких пользователях тестируем:*** на всех пользователях.

***Ключевые метрики:***
* Время, проведенное на сайте (TSS) - primary.
* Глубина просмотра страниц (PPV) - secondary

***Ожидаемый эффект:*** Увеличение TSS на 10% и увеличение PPV на 7%

***План действий:*** 
* Если эксперимент даст положительный результат, т.е. мы зафиксируем ожидаемое улучшение в ключевых метриках  и не посадим добавочные, то произведем масштабирование изменения на всех пользователей.
* Если основные метрики просядут или вырастут незначительно, либо добавочные метрики упадут - откатываем эксперимент

***Рассчитаем объем необходимой выборки и время проведения эксперимента***
Текущий показатель TSS равен 44,43 мин, а стандартная ошибка (SD) равна 140. Согласно выдвинутой гипотезе мы предполагаем, что в новой версии TSS увеличится на 10%. Средний трафик составляет 15000 человек в день. alpha = 5% и beta = 20%.

In [2]:
# Расчёт effect_size для непрерывных метрик
def calc_continuous_es(mean_control: Union[float, int],
                                std_control: Union[float, int],
                                mean_test: Union[float, int],
                                std_test: Union[float, int]):
    return abs(effectsize_smd(mean_control,
                             std_control,
                             1e4,
                             mean_test,
                             std_test,
                             1e4)[0])

In [3]:
# Расчёт минимально необходимой выборки * 2(для теста и контроля) для непрерывной метрики
def calc_sample_size_continuous(effect_size: float,
                                alpha: float = .05,
                                beta: float = .2,
                                ratio: Union[float, int] = 1):
    
    n = tt_ind_solve_power(effect_size=effect_size,
                           alpha=alpha,
                           power=(1 - beta),
                           ratio=ratio,
                  )
    return int(n * 2)

In [4]:
# вводим данные
tss_control, tss_test = 44.43, 44.43 * 1.1 
std_control, std_test = 140, 140
traffic = 15_000

In [5]:
# рассчитываем effect size
es_cont = calc_continuous_es(tss_control, std_control, tss_test, std_test)
es_cont

0.031734524062528496

In [6]:
print(f"При рассчитанном effect size={es_cont}, принимая во внимание значение alpha = 5% и beta = 20%, получаем "
      f"необходимое количество наблюдений равное {calc_sample_size_continuous(es_cont)}."
      f" Учитывая, что средний трафик составляет {traffic} человек в день и необходимое количество наблюдений, получаем,"
      f" что эксперимен должен длиться {math.ceil(calc_sample_size_continuous(es_cont) / traffic)} дней.")

При рассчитанном effect size=0.031734524062528496, принимая во внимание значение alpha = 5% и beta = 20%, получаем необходимое количество наблюдений равное 31176. Учитывая, что средний трафик составляет 15000 человек в день и необходимое количество наблюдений, получаем, что эксперимен должен длиться 3 дней.


*Проверим, хватит ли нам времени, чтобы корректно оценить еще одну заявленную метрику - PPV*
Текущий показатель PPV равен 6.4 мин, а стандартная ошибка (SD) равна 83. Согласно выдвинутой гипотезе мы предполагаем, что в новой версии PPV увеличится на 7%. Средний трафик составляет 15000 человек в день. alpha = 5% и beta = 20%.

In [7]:
# вводим данные
ppv_control, ppv_test = 6.4, 6.4 * 1.07 
std_control, std_test = 83, 83

In [8]:
# рассчитываем effect size
es_cont = calc_continuous_es(ppv_control, std_control, ppv_test, std_test)
es_cont

0.005397387929033588

In [9]:
print(f"При рассчитанном effect size={es_cont}, принимая во внимание значение alpha = 5% и beta = 20%, получаем "
      f"необходимое количество наблюдений равное {calc_sample_size_continuous(es_cont)}."
      f" Учитывая, что средний трафик составляет {traffic} человек в день и необходимое количество наблюдений, получаем,"
      f" что эксперимен должен длиться {math.ceil(calc_sample_size_continuous(es_cont) / traffic)} дней.")

При рассчитанном effect size=0.005397387929033588, принимая во внимание значение alpha = 5% и beta = 20%, получаем необходимое количество наблюдений равное 1077705. Учитывая, что средний трафик составляет 15000 человек в день и необходимое количество наблюдений, получаем, что эксперимен должен длиться 72 дней.


Для оченки основного критерия нам требуется держать эксперимент 3 дня, в то время как для оценки дополнительного - 72 дня. Данный факт был доведен до ответственных лиц и было принято решение о приоритетной оценке основного параметра, соответственно, утвержденная длительность эксперимента - 3 рабочих дня (в выходные дни тест проводиться не будет). Поведение второстпеной метрики не будет учитываться при принятии итогового решения.

### 3. Запуск теста
Проверим систему сплитования юзеров.

Мы провели А/А тест, в котором сравнивали время проведенное на одной и той же версии сайта. Полученные результаты выглядят следующим образом. 
<table>
    <tr>
        <td></td>
        <td>Версия А1</td>
        <td>Версия А2</td>
    </tr>
    <tr>
        <td>Среднее</td>
        <td>44,43</td>
        <td>44,16</td>
    </tr>
    <tr>
        <td>Стандартное отклонение</td>
        <td>14,51</td>
        <td>13,94</td>
    </tr>
    <tr>
        <td>Выборка</td>
        <td>3000</td>
        <td>3000</td>
    </tr>
</table>
Уровень доверия 95%.

In [10]:
# Вводим исходные данные по выборкам
alpha = .05
sample_1_mean, sample_2_mean = 44.43, 44.16
sample_1_se, sample_2_se = 14.51, 13.94
sample_1_size, sample_2_size = 3_000, 3_000

# Генерируем нормальное распределение на основе введенных данных
norm_1 = st.norm(loc=sample_1_mean, scale=sample_1_se).rvs(size=sample_1_size, random_state=42)
norm_2 = st.norm(loc=sample_2_mean, scale=sample_2_se).rvs(size=sample_2_size, random_state=42)

In [11]:
fig = go.Figure()
fig.add_trace(go.Histogram(x=norm_1, name='norm_1'))
fig.add_trace(go.Histogram(x=norm_2, name='norm_2'))

# Overlay both histograms
fig.update_layout(barmode='overlay')
# Reduce opacity to see both histograms
fig.update_traces(opacity=0.5)
fig.show()

In [12]:
# Альтернативный способ через бутсрап
booted_diff = []
booted_pvalue = []
size = max(norm_1.size, norm_2.size)
for _ in tqdm(range(10_000)):
    a_s = np.random.choice(norm_1, size=size, replace=True)
    b_s = np.random.choice(norm_2, size=size, replace=True)
    booted_diff.append(np.mean(a_s - b_s))
    booted_pvalue.append(st.ttest_ind(a_s, b_s, equal_var=False, alternative='two-sided')[1])

# Доверительный интервал разниц между группами
md_ci, std_ci = np.mean(booted_diff), np.std(booted_diff, ddof=1)
left_ci, right_ci = np.percentile(booted_diff, [2.5, 97.5])
p_value_ci = 2 * (1 - st.norm.cdf(np.abs(md_ci / std_ci)))

100%|██████████| 10000/10000 [00:07<00:00, 1295.33it/s]


In [13]:
print(f"Mean difference: {np.round(md_ci, 5)}, p-value: {p_value_ci} and confidence interval is: [{np.round(left_ci, 5)}, {np.round(right_ci, 5)}]")

if p_value_ci < alpha and not min(left_ci, right_ci) < 0 < max(left_ci, right_ci):
    print(f"Sample # {1 if md_ci > 0 else 2} mean is greater")
else:
    print("No significant difference")

Mean difference: 0.29027, p-value: 0.42126722597102484 and confidence interval is: [-0.41621, 1.00264]
No significant difference


In [14]:
# Ошибка первого рода, которая говорит нам о том, что группы почти не различаются между собой!
np.mean(np.array(booted_pvalue) < 0.05) # FPR

0.1263

In [15]:
fig = make_subplots(rows=2, cols=1)

fig.add_trace(
    go.Histogram(x=booted_pvalue, name='booted_pvalue',),
    row=1, col=1
)

fig.add_trace(
    go.Histogram(x=booted_diff, name='booted_diff',),
    row=2, col=1
)

fig.update_layout(height=800, width=1000, title_text="After bootstrap")
fig.show()

Получили околоравномерное распределение pvalue, с явным выбросом в левой стороне. Полученный доверительный интервал включает в себя 0 и говорит о том, что разницы между результатами нет, но FPR составляет порядка 12%, т.е 12% бутстрапированных наблюдений показали разницу между средними, что, в свою очередь, говорит о разнице между группами.

Однако, стейкхолдеры посчитали процент приемлимым и приняли решение провести эксперимент.

### 4. Сбор и анализ данных. Интерпретация результата
На основе данных А/В теста, в котором для тестовай группы изменили систему настройки фильтров на более упрощеную и понятную, а для контрольной группы оставили текущую версию сайта, получили следующие результаты: 
<table>
    <tr>
        <td></td>
        <td>Control</td>
        <td>Test</td>
    </tr>
    <tr>
        <td>Посещение</td>
        <td>16101</td>
        <td>16903</td>
    </tr>
    <tr>
        <td>TSS</td>
        <td>45.16</td>
        <td>49.23</td>
    </tr>
     <tr>
        <td>станд.отклонение TSS</td>
        <td>120</td>
        <td>123,3</td>
    </tr>
</table>

Проанализируем результаты, полученные по нашей основной метрике TSS

In [16]:
alpha = .05
sample_1_mean, sample_2_mean = 45.16, 49.23 
sample_1_se, sample_2_se = 120, 123.3
sample_1_size, sample_2_size = 16_101, 16_903
# Генерируем нормальное распределение на основе введенных данных
norm_1 = st.norm(loc=sample_1_mean, scale=sample_1_se).rvs(size=sample_1_size, random_state=42)
norm_2 = st.norm(loc=sample_2_mean, scale=sample_2_se).rvs(size=sample_2_size, random_state=42)

In [17]:
fig = go.Figure()
fig.add_trace(go.Histogram(x=norm_1, name='norm_1'))
fig.add_trace(go.Histogram(x=norm_2, name='norm_2'))

# Overlay both histograms
fig.update_layout(barmode='overlay')
# Reduce opacity to see both histograms
fig.update_traces(opacity=0.5)
fig.show()

In [18]:
# Альтернативный способ через бутсрап
booted_diff = []
booted_pvalue = []

size = max(norm_1.size, norm_2.size)
for _ in tqdm(range(10_000)):
    a_s = np.random.choice(norm_1, size=size, replace=True)
    b_s = np.random.choice(norm_2, size=size, replace=True)
    booted_diff.append(np.mean(a_s - b_s))
    booted_pvalue.append(st.ttest_ind(a_s, b_s, equal_var=False, alternative='two-sided')[1])

# Доверительный интервал разниц между группами
md_ci, std_ci = np.mean(booted_diff), np.std(booted_diff, ddof=1)
left_ci, right_ci = np.percentile(booted_diff, [2.5, 97.5])
p_value_ci = 2 * (1 - st.norm.cdf(np.abs(md_ci / std_ci)))

100%|██████████| 10000/10000 [00:14<00:00, 705.12it/s]


In [19]:
print(f"Mean difference: {np.round(md_ci, 5)}, p-value: {p_value_ci} and confidence interval is: [{np.round(left_ci, 5)}, {np.round(right_ci, 5)}]")

if p_value_ci < alpha and not min(left_ci, right_ci) < 0 < max(left_ci, right_ci):
    print(f"Sample # {1 if md_ci > 0 else 2} mean is greater")
else:
    print("No significant difference")

Mean difference: -4.22131, p-value: 0.0012821358787624693 and confidence interval is: [-6.7458, -1.62219]
Sample # 2 mean is greater


In [20]:
# рассчитаем аплифн
uplift =(sample_2_mean - sample_1_mean) / sample_1_mean
uplift

0.09012400354295838

По результатам проведенных тестов наблюдаем следующие результаты:

* значение p_value меньше alpfa - подтверждается наличие статистически значимых различий между группами
* доверительный интервал для разницы групп не включает в себя 0 - также говорит о наличии статистически значимых различиях
* отрицательная разница средних говорит о том, что показатели тестовой группы лучше.
* аплифт конверсии тестовой группы меньше прогнозируемого (мнеьше 10%)

### 5. Принятие решения на основе результатов теста
Не смотря на то, что результаты А/В теста говорят о преимуществе тестовой группы, принято решение откатить эксперимент и не менять систему настройки фильтров при подборе товаров, т.к. аплифт тестовой группы фактически оказался меньше ожидаемого.

## `Гипотеза 2`
### 2. Дизайн эксперимента 1
***Гипотеза 1:*** Если добавить справочную информацию по параметрам сравнения в разделе "Сравнение товаров" для всех пользователей, то мы увеличим конверсию в покупку на 13% потому что пользователь любит платить за то, что он понимает, а непонятные термины и характеристики его отпугивают.

***Что делаем:***
* *Контрольная версия* - действующая версия сайта.
* *Тестовая версия* - добавляем tooltips при наведение курсора на знак "?" рядом с названием параметра сравнения.

***На каких пользователях тестируем:*** на всех пользователях.

***Ключевые метрики:***
* Конверсия в покупку (CR)

***Ожидаемый эффект:*** Увеличение CR на 13%

***План действий:*** 
* Если эксперимент даст положительный результат, т.е. мы зафиксируем ожидаемое улучшение в в основной метрике  и при этом не просадим остальные, то произведем масштабирование изменения на всех пользователей.
* Если основная метрика просядет или вырастет незначительно, либо добавочные метрики упадут - откатываем эксперимент

***Рассчитаем объем необходимой выборки и время проведения эксперимента***
Текущий показатель CR равен 5,1%. Мы предполагаем, что при добавления справочной информации при подборе она изменится минимум на 13%. Средний трафик составляет 15000 человек в день. alpha = 5% и beta = 20%.

In [21]:
# Расчёт effect_size для пропорций
def calc_proportion_es(prob1: float, prob2: float):
    return abs(proportion_effectsize(prob1, prob2))

In [22]:
# Расчёт минимально необходимой выборки * 2(для теста и контроля) для пропорций
def calc_sample_size_proportion(effect_size: float,
                                alpha: float = .05,
                                beta: float = .2,
                                ratio: Union[float, int] = 1):
    
    n = zt_ind_solve_power(effect_size=effect_size,
                           alpha=alpha,
                           power=(1 - beta),
                           ratio=ratio,
                  )
    return int(n * 2)

In [23]:
# вводим данные
conv1, conv2 = 0.051, 0.051 * 1.13
traffic = 15_000

# считаем effectsize
es_prop = calc_proportion_es(conv1, conv2)
es_prop

0.02926683811259201

In [24]:
# параметры alpha и beta при расчете количества испытаний в нашем случае можно не указывать, т.к. они стоят по умолчанию

print(f"При рассчитанном effect size={es_prop}, принимая во внимание значение alpha = 5% и beta = 20%, получаем "
      f"необходимое количество наблюдений равное {calc_sample_size_proportion(es_prop)}."
      f" Учитывая, что средний трафик составляет {traffic} человек в день и необходимое количество наблюдений, получаем,"
      f" что эксперимен должен длиться {math.ceil(calc_sample_size_proportion(es_prop) / traffic)} дней.")

При рассчитанном effect size=0.02926683811259201, принимая во внимание значение alpha = 5% и beta = 20%, получаем необходимое количество наблюдений равное 36653. Учитывая, что средний трафик составляет 15000 человек в день и необходимое количество наблюдений, получаем, что эксперимен должен длиться 3 дней.


Для оченки основного критерия нам требуется держать эксперимент 3 дня.

### 3. Запуск теста
Проверим систему сплитования юзеров.

Мы провели А/А тест, в котором сравнивали одну и ту же версию сайта. Полученные результаты выглядят следующим образом. 
<table>
    <tr>
        <td></td>
        <td>Версия А1</td>
        <td>Версия А2</td>
    </tr>
    <tr>
        <td>Выборка</td>
        <td>10731</td>
        <td>10902</td>
    </tr>
    <tr>
        <td>Конверсия</td>
        <td>542</td>
        <td>567
        </td>
    </tr>
</table>
Уровень доверия 95%.

In [25]:
# Задаем начальные параметры
alpha = .05
prob_1, prob_2 = 542 / 10731, 567 / 10902 
sample_1_size, sample_2_size = 10731, 10902

# Генерируем распределение.
a = st.bernoulli.rvs(p=prob_1, size=sample_1_size, random_state=12)
b = st.bernoulli.rvs(p=prob_2, size=sample_2_size, random_state=25)

In [26]:
# Сравнение хи2 и z
chi_value, p_value_chi2, table = proportion.proportions_chisquare([a.sum(), b.sum()], [a.size, b.size])
z_value, p_value_z = proportion.proportions_ztest([a.sum(), b.sum()], [a.size, b.size])
print(p_value_chi2, p_value_z)

0.22731342954866793 0.22731342954866907


In [27]:
# Альтернативный способ через бутсрап
booted_diff = []
booted_pvalue = []
size = max(a.size, b.size)

for _ in tqdm(range(10_000)):
    a_s = st.bernoulli.rvs(p=prob_1, size=size)
    b_s = st.bernoulli.rvs(p=prob_2, size=size)
    booted_diff.append(np.mean(a_s - b_s))
    booted_pvalue.append(proportion.proportions_chisquare([a_s.sum(), b_s.sum()], [a_s.size, b_s.size])[1])

md_ci, std_ci = np.mean(booted_diff), np.std(booted_diff, ddof=1)
left_ci, right_ci = np.percentile(booted_diff, [2.5, 97.5])
p_value_ci = 2 * (1 - st.norm.cdf(np.abs(md_ci / std_ci)))

100%|██████████| 10000/10000 [00:12<00:00, 793.92it/s]


In [28]:
# Доверительный интервал разниц между группами
print(f"Mean difference: {np.round(md_ci, 5)}, p-value: {p_value_ci} and confidence interval is: [{np.round(left_ci, 5)}, {np.round(right_ci, 5)}]")

if p_value_ci < alpha and not min(left_ci, right_ci) < 0 < max(left_ci, right_ci):
    print(f"Sample # {1 if md_ci > 0 else 2} mean is greater")
else:
    print("No significant difference")

Mean difference: -0.00156, p-value: 0.5991073749031428 and confidence interval is: [-0.00734, 0.00422]
No significant difference


In [29]:
# Ошибка первого рода
np.mean(np.array(booted_pvalue) < 0.05) # FPR

0.0784

In [30]:
fig = make_subplots(rows=2, cols=1)

fig.add_trace(
    go.Histogram(x=booted_pvalue, name='booted_pvalue',),
    row=1, col=1
)

fig.add_trace(
    go.Histogram(x=booted_diff, name='booted_diff',),
    row=2, col=1
)

fig.update_layout(height=800, width=1000, title_text="After bootstrap")
fig.show()

Получили близкое к равномернму распределение pvalue, с выбросом в левой стороне. Полученный доверительный интервал включает в себя 0 и говорит о том, что разницы между результатами нет. FPR составляет порядка 8%, т.е 8% бутстрапированных наблюдений показали разницу между средними, что, в свою очередь, говорит о приемлимой разнице между группами.

Стейкхолдеры посчитали FPR приемлимым и приняли решение провести эксперимент.

### 4. Сбор и анализ данных. Интерпретация результата
На основе данных А/В теста, в котором для тестовой группы добавили tooltips при наведение курсора на знак "?" рядом с названием параметра сравнения, а для контрольной оставили текущую версию сайта, получили следующие результаты: 
<table>
    <tr>
        <td></td>
        <td>Control</td>
        <td>Test</td>
    </tr>
    <tr>
        <td>Посещение</td>
        <td>18632</td>
        <td>18406</td>
    </tr>
    <tr>
        <td>Конверсия</td>
        <td>955</td>
        <td>1068</td>
    </tr>
</table>

Проанализируем результаты, полученные по нашей метрике CR

In [31]:
# Задаем начальные параметры
alpha = .05
prob_1, prob_2 = 955 / 18632, 1068 / 18406 
sample_1_size, sample_2_size = 18632, 18406

# Генерируем распределение.
a = st.bernoulli.rvs(p=prob_1, size=sample_1_size, random_state=12)
b = st.bernoulli.rvs(p=prob_2, size=sample_2_size, random_state=25)

In [32]:
# Сравнение хи2 и z
chi_value, p_value_chi2, table = proportion.proportions_chisquare([a.sum(), b.sum()], [a.size, b.size])
z_value, p_value_z = proportion.proportions_ztest([a.sum(), b.sum()], [a.size, b.size])
print(p_value_chi2, p_value_z)

0.0014138373144481232 0.0014138373144481054


In [33]:
# Альтернативный способ через бутсрап
booted_diff = []
booted_pvalue = []
size = max(a.size, b.size)

for _ in tqdm(range(10_000)):
    a_s = st.bernoulli.rvs(p=prob_1, size=size)
    b_s = st.bernoulli.rvs(p=prob_2, size=size)
    booted_diff.append(np.mean(a_s - b_s))
    booted_pvalue.append(proportion.proportions_chisquare([a_s.sum(), b_s.sum()], [a_s.size, b_s.size])[1])

md_ci, std_ci = np.mean(booted_diff), np.std(booted_diff, ddof=1)
left_ci, right_ci = np.percentile(booted_diff, [2.5, 97.5])
p_value_ci = 2 * (1 - st.norm.cdf(np.abs(md_ci / std_ci)))

100%|██████████| 10000/10000 [00:17<00:00, 583.38it/s]


In [34]:
# Доверительный интервал разниц между группами
print(f"Mean difference: {np.round(md_ci, 5)}, p-value: {p_value_ci} and confidence interval is: [{np.round(left_ci, 5)}, {np.round(right_ci, 5)}]")

if p_value_ci < alpha and not min(left_ci, right_ci) < 0 < max(left_ci, right_ci):
    print(f"Sample # {1 if md_ci > 0 else 2} mean is greater")
else:
    print("No significant difference")

Mean difference: -0.00678, p-value: 0.004238557953559985 and confidence interval is: [-0.01138, -0.00215]
Sample # 2 mean is greater


In [35]:
# рассчитаем аплифн
uplift =(prob_2 - prob_1) / prob_1
uplift

0.13205607322447221

По результатам проведенных тестов наблюдаем следующие результаты:

* значение p_value меньше alpfa подтверждает существование статистически значимых различий между группами
* доверительный интервал для разницы групп не включает в себя 0 - также говорит о наличие статистически значимых различиях
* отрицательная разница средних говорит о том, что показатели тестовой группы лучше. 
* аплифт конверсии тестовой группы соответствует прогнозируемому (13%)

### 5. Принятие решения на основе результатов теста
На основе результатов А/В теста принято решение масштабировать эксперимент на всех пользователей